In [31]:
import numpy as np
import pandas as pd
from tqdm import tqdm


In [32]:
#   Read main dataset and annotation about cell type adn centriole existence 

df = pd.read_csv('./data/S7_table.csv')
annotation = pd.read_csv('./data/annotation.csv')


In [33]:
# Delete from main dataset undefferentiated cell type and adjusted.tmp equals 0.0  

def remove_undef(x):
    list_x = x.split('_')
    if list_x.count('undifferentiated') > 0:
        return True        
    else:
        return False 

undef = df["cell.bin"].apply(lambda x: remove_undef(x))
df['undef'] = undef

df.drop(df[df['adjusted.tpm.estimate'] == 0.0].index, inplace = True)
df.drop(df[df['undef'] == True].index, inplace = True)
df.drop('undef', inplace=True, axis=1)


In [34]:
# Create a dictionary of existing centriol

annotation = annotation.drop(columns = ['cell_status'])
annotation['centriole'] = np.where(annotation['centriole'] == 'absent', 0, annotation['centriole'])
annotation['centriole'] = np.where(annotation['centriole'] == 'present', 1, annotation['centriole'])

# dictionary
annotation_dictionary = annotation.set_index('cell_type').T.to_dict('records')

In [35]:
# add column which shows centriole
def convert(x):
    list_x = x.split(":")
    type_cell = list_x[0]
    return annotation_dictionary[0][type_cell]
cell_type = df["cell.bin"].apply(lambda x: convert(x))
df['centiole'] = cell_type

In [36]:
df.head()

gene         gene.id     cell.bin  raw.tpm.estimate  \
0  aap-1  WBGene00000001  ADE:390_510              35.7   
2  aap-1  WBGene00000001  ADF:390_510              38.6   
6  aap-1  WBGene00000001  ADL:330_390              57.3   
7  aap-1  WBGene00000001  ADL:390_510              62.4   
8  aap-1  WBGene00000001  ADL:510_650              56.0   

   adjusted.tpm.estimate  bootstrap.median.tpm  ci.95p.lb  ci.80p.lb  \
0                   14.5                  30.9        0.0        0.5   
2                   30.7                  37.6        3.2       13.3   
6                   55.0                  56.7       19.7       31.2   
7                   59.4                  61.9       28.6       40.5   
8                   49.4                  54.3       13.3       26.8   

   ci.80p.ub  ci.95p.ub centiole  
0       71.5       92.2        0  
2       64.3       80.3        0  
6       84.0       97.1        0  
7       85.9      100.0        0  
8       83.9      106.2        0

In [37]:
# Extract unique genes
unique_genes = df['gene'].unique()
unique_genes.size

17194

In [38]:
full_dict = dict()
 
for gene, group in tqdm(df.groupby(['gene'])):
     group.drop('gene.id', inplace=True, axis=1)
     group.drop('gene', inplace=True, axis=1)
     cell_type_dictionary = group.set_index('cell.bin').T.to_dict('list')
     full_dict[gene] = cell_type_dictionary


100%|██████████| 17194/17194 [01:14<00:00, 230.73it/s]


In [39]:
full_dict

{'2L52.1': {'ADE:390_510': [46.8, 29.4, 43.1, 0.0, 8.5, 87.8, 112.7, 0],
  'ADEsh:390_510': [42.1, 19.6, 41.3, 0.0, 0.0, 84.0, 112.5, 0],
  'ADL:330_390': [27.3, 19.7, 27.0, 0.0, 8.8, 46.2, 61.7, 0],
  'ADL:390_510': [4.0, 2.3, 3.5, 0.0, 0.3, 7.6, 10.2, 0],
  'ASE:390_510': [6.3, 1.2, 6.2, 0.0, 0.0, 13.4, 18.6, 0],
  'ASH:330_390': [18.0, 12.1, 14.8, 0.0, 6.7, 32.6, 43.6, 0],
  'ASJ:510_650': [22.1, 11.4, 21.7, 0.0, 0.0, 44.1, 57.1, 0],
  'ASK:390_510': [11.2, 6.1, 11.1, 0.0, 0.0, 22.7, 28.7, 0],
  'AVA:330_390': [48.5, 34.1, 47.3, 7.7, 18.5, 84.4, 109.5, 0],
  'AVE:330_390': [24.9, 12.1, 24.5, 0.0, 0.0, 49.3, 64.4, 0],
  'B_F_K_Kp_U_Y:510_580': [12.4, 1.6, 11.1, 0.0, 0.0, 25.3, 35.9, 'ambiguous'],
  'BWM_anterior:210_270': [13.7, 11.0, 13.3, 2.6, 6.1, 22.0, 27.4, 0],
  'BWM_anterior:270_330': [5.4, 4.8, 5.4, 2.4, 3.5, 7.6, 8.7, 0],
  'BWM_anterior:330_390': [7.7, 7.0, 7.6, 4.2, 5.2, 10.2, 11.9, 0],
  'BWM_anterior:390_450': [8.7, 8.2, 8.5, 5.0, 6.1, 11.1, 12.8, 0],
  'BWM_anterior:450